<a href="https://colab.research.google.com/github/Hrtsh-Ynkzn/SAMURAI/blob/main/Study/titanic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#### <div style= "font-family: Cambria; font-weight:bold; letter-spacing: 0px; color:white; font-size:150%; text-align:left;padding:3.0px; background: #006036; border-bottom: 8px solid #D0A900" > TABLE OF CONTENTS<br><div>
* [IMPORTS](#1)
* [PREPROCESSING](#2)
* [FEATURES SELECT](#3)
* [MODEL TRAINING](#4)
* [PREDICT](#5)
* [SUBMISSION](#6)

<a id="1"></a>
# <div style= "font-family: Cambria; font-weight: bold; letter-spacing: 0px; color: white; font-size: 120%; text-align: left; padding: 3.0px; background: #006036; border-bottom: 8px solid #D0A900" > IMPORTS<br> <div>

In [1]:
import seaborn as sns
import numpy as np
import pandas as pd
import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# 分析ライブラリ
import lightgbm as lgb
import optuna.integration.lightgbm as lgb_optuna
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.metrics import classification_report

import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
# 学習データとテストデータのデータフレームへの読み込み
train = pd.read_csv('/kaggle/input/titanic/train.csv')
test  = pd.read_csv('/kaggle/input/titanic/test.csv')

<a id="2"></a>
# <div style= "font-family: Cambria; font-weight: bold; letter-spacing: 0px; color: white; font-size: 120%; text-align: left; padding: 3.0px; background: #006036; border-bottom: 8px solid #D0A900" > PREPROCESSING<br> <div>

In [ ]:
# 学習データとテストデータの「male」、「female」の文字列を「0」、「1」に数値化する
train = train.replace({'male' : 0, 'female' : 1})
test  = test.replace({'male' : 0, 'female' : 1})

In [ ]:
# 学習データとテストデータの「Age」について、Pclass毎に中央値で穴埋めをする
train.loc[train['Age'].isnull(), 'Age'] = train.groupby('Pclass')['Age'].transform('median')
test.loc[test['Age'].isnull(), 'Age']   = test.groupby('Pclass')['Age'].transform('median')

In [ ]:
# 学習データの「Embarked」の欠損値の2つを最頻値で穴埋めする
train['Embarked'] = train['Embarked'].fillna(train['Embarked'].mode())

In [ ]:
# テストデータの「Fare」の欠損値の１つを中央値で穴埋めする
test['Fare'] = test['Fare'].fillna(test['Fare'].median())

In [ ]:
train['Title_tr'] = train['Name'].map(lambda x: x.split(', ')[1].split('. ')[0])

train['Title_tr'] = train['Title_tr'].replace(['Dr','Rev','Mlle','Major','Col','the Countess','Capt','Ms','Sir','Lady','Mme','Don','Jonkheer'], "Others")
train['Title_tr'] = train['Title_tr'].map( {'Master': 0 , 'Miss':1 , 'Mr':2, 'Mrs':3, 'Others':4})

In [ ]:
test['Title_te'] = test['Name'].map(lambda x: x.split(', ')[1].split('. ')[0])
test['Title_te'] = test['Title_te'].replace(['Col','Rev','Ms','Dr','Dona'], 'Others')
test['Title_te'] = test['Title_te'].map( {'Master': 0 , 'Miss':1 , 'Mr':2, 'Mrs':3, 'Others':4})

In [ ]:
# 学習データにダミー変数化を実行
train_embarked_dum = pd.get_dummies(train['Embarked'], dtype = 'uint8')
train_add_dum      = pd.concat([train, train_embarked_dum], axis = 1)
train_add_dum.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name  Sex   Age  SibSp  Parch  \
0                            Braund, Mr. Owen Harris    0  22.0      1      0   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...    1  38.0      1      0   
2                             Heikkinen, Miss. Laina    1  26.0      0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)    1  35.0      1      0   
4                           Allen, Mr. William Henry    0  35.0      0      0   

             Ticket     Fare Cabin Embarked  Title_tr  C  Q  S  
0         A/5 21171   7.2500   NaN        S         2  0  0  1  
1          PC 17599  71.2833   C85        C         3  1  0  0  
2  STON/O2. 3101282   7.9250   NaN        S         1  0  0  1  
3            113803  53.1000  C123        S         3  0  0  1  
4            373450   8.0500   NaN        S         2  0  0  1

In [ ]:
# テストデータにダミー変数化を実行
test_embarked_dum = pd.get_dummies(test['Embarked'], dtype = 'uint8')
test_add_dum      = pd.concat([test, test_embarked_dum], axis = 1)
test_add_dum.head()

PassengerId  Pclass                                          Name  Sex  \
0          892       3                              Kelly, Mr. James    0   
1          893       3              Wilkes, Mrs. James (Ellen Needs)    1   
2          894       2                     Myles, Mr. Thomas Francis    0   
3          895       3                              Wirz, Mr. Albert    0   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)    1   

    Age  SibSp  Parch   Ticket     Fare Cabin Embarked  Title_te  C  Q  S  
0  34.5      0      0   330911   7.8292   NaN        Q         2  0  1  0  
1  47.0      1      0   363272   7.0000   NaN        S         3  0  0  1  
2  62.0      0      0   240276   9.6875   NaN        Q         2  0  1  0  
3  27.0      0      0   315154   8.6625   NaN        S         2  0  0  1  
4  22.0      1      1  3101298  12.2875   NaN        S         3  0  0  1

<a id="3"></a>
# <div style= "font-family: Cambria; font-weight: bold; letter-spacing: 0px; color: white; font-size: 120%; text-align: left; padding: 3.0px; background: #006036; border-bottom: 8px solid #D0A900" > FEATURES SELECT<br> <div>

In [ ]:
train_features = train_add_dum[['Pclass', 'Sex', 'Age', 'Fare', 'Title_tr', 'C', 'Q', 'S']].values
train_target   = train['Survived'].values

<a id="4"></a>
# <div style= "font-family: Cambria; font-weight: bold; letter-spacing: 0px; color: white; font-size: 120%; text-align: left; padding: 3.0px; background: #006036; border-bottom: 8px solid #D0A900" > MODEL TRAINING<br> <div>

LightGBM, ベイズ最適化によるパラメータチューニング、層化k分割交差検証を実行する<br>
create_model_classification関数の作成

In [ ]:
def create_model_classification(train_features, train_target, features_cols, target_col):

    print('Target :', target_col)

    # LightGBM parametersをディクショナリで作成する
    lgb_params = {'objective' : 'binary',       # 目的関数の設定
                  'metric'    : 'auc'}

    # KFoldクラスによるk分割交差検証のインスタンスを生成
    K_fold = StratifiedKFold(n_splits = 5,
                             shuffle = True,
                             random_state = 39)

    # 説明変数Xと目的変数yの準備
    X = train_features
    y = train_target

    # 作成したmodelを格納するリストの作成
    models = []

    # 分割回数を数えながら、分割した各変数を用いて学習し、modelを格納する
    for fold, (train_index, valid_index) in enumerate(K_fold.split(X, y)):

        # 説明変数と検証変数を格納
        X_train, X_valid = X[train_index], X[valid_index]
        y_train, y_valid = y[train_index], y[valid_index]

        # ベイズ最適化の準備
        lgb_train = lgb_optuna.Dataset(X_train, y_train, feature_name = features_cols)
        lgb_eval  = lgb_optuna.Dataset(X_valid, y_valid, feature_name = features_cols)

        # oputunaを用いてパラメータをチューニングしながら、LightGBMのモデル学習を行う
        lgbm = lgb_optuna.train(lgb_params,
                                lgb_train,
                                valid_sets = [lgb_train, lgb_eval],
                                num_boost_round = 100)

        # 作成した学習モデルで予測値を算出する
        y_pred = lgbm.predict(X_valid)

        # 作成したモデルをリストに格納
        models.append(lgbm)

        # 各モデルのAUCを作成
        auc = metrics.roc_auc_score(y_valid, y_pred)

        print(f'fold: {fold}, AUC: {auc}')

    return models

In [ ]:
# 引数の準備
features_cols = set(['Pclass', 'Sex', 'Age', 'Fare', 'Title_tr', 'C', 'Q', 'S'])
target_col    = list(['Survived'])

# 学習
models = create_model_classification(train_features, train_target, features_cols, target_col)

[I 2023-12-30 08:14:49,608] A new study created in memory with name: no-name-b8fe3f7a-75b5-4d76-96ef-7e93ff431ae5


Target : ['Survived']


feature_fraction, val_score: -inf:   0%|          | 0/7 [00:00<?, ?it/s]

[LightGBM] [Info] Number of positive: 273, number of negative: 439
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002964 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 196
[LightGBM] [Info] Number of data points in the train set: 712, number of used features: 8
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.383427 -> initscore=-0.475028
[LightGBM] [Info] Start training from score -0.475028
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[1]	valid_0's auc: 0.887698	valid_1's auc: 0.873057
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[2]	valid_0's auc: 0.899526	valid_1's auc: 0.874506
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[3]	valid_0's auc: 0.906343	valid_1's auc: 0.884717
[LightGBM] [Warning] No further splits with positive gain, best ga

feature_fraction, val_score: 0.903162:  14%|#4        | 1/7 [00:00<00:03,  1.57it/s]

...

[LightGBM] [Info] Number of positive: 273, number of negative: 440
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000938 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 196
[LightGBM] [Info] Number of data points in the train set: 713, number of used features: 8
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.382889 -> initscore=-0.477303
[LightGBM] [Info] Start training from score -0.477303
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[1]	valid_0's auc: 0.725096	valid_1's auc: 0.665138
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[2]	valid_0's auc: 0.8331	valid_1's auc: 0.817976
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[3]	valid_0's auc: 0.854783	valid_1's auc: 0.853876
[LightGBM] [Warning] No further splits with positive gain, best gain

min_child_samples, val_score: 0.913442: 100%|##########| 5/5 [00:02<00:00,  2.39it/s]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[96]	valid_0's auc: 0.89165	valid_1's auc: 0.888911
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[97]	valid_0's auc: 0.891679	valid_1's auc: 0.88931
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[98]	valid_0's auc: 0.89202	valid_1's auc: 0.889576
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[99]	valid_0's auc: 0.891937	valid_1's auc: 0.891171
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[100]	valid_0's auc: 0.892403	valid_1's auc: 0.890773


[I 2023-12-30 08:17:49,870] Trial 67 finished with value: 0.8907725036564287 and parameters: {'min_child_samples': 100}. Best is trial 63 with value: 0.9134423613881133.
min_child_samples, val_score: 0.913442: 100%|##########| 5/5 [00:02<00:00,  1.97it/s]

fold: 4, AUC: 0.9134423613881135


<a id="4"></a>
# <div style= "font-family: Cambria; font-weight: bold; letter-spacing: 0px; color: white; font-size: 120%; text-align: left; padding: 3.0px; background: #006036; border-bottom: 8px solid #D0A900" > PREDICT<br> <div>

In [ ]:
# テストデータの特徴量を選定
test_features = test_add_dum[['Pclass', 'Sex', 'Age', 'Fare', 'Title_te', 'C', 'Q', 'S']].values

In [ ]:
# 作成したモデルの一つを用いて予測
predict_test_target = models[0].predict(test_features)

In [ ]:
predict_test_target.shape

(418,)

In [ ]:
# 確認
print(predict_test_target)

[0.04649295 0.19126624 0.0700778  0.37368715 0.53245369 0.19437293
 0.21746094 0.08208143 0.78191399 0.03548304 0.01457845 0.08923272
 0.9788135  0.02190563 0.93622547 0.93094034 0.05474114 0.28491136
 0.7749627  0.37382046 0.4490005  0.53233676 0.9832109  0.82768086
 0.97984479 0.01209301 0.99189582 0.3050785  0.60826667 0.37878349
 0.04288401 0.23291659 0.73774771 0.82430306 0.79746592 0.07407262
 0.08393537 0.18723715 0.0706788  0.57057353 0.03679823 0.65681595
 0.02223163 0.95042692 0.97895709 0.13008775 0.20585506 0.08765264
 0.98246337 0.76380194 0.59746898 0.09363456 0.97556848 0.9537587
 0.31916333 0.07923542 0.01402494 0.0821563  0.09801484 0.9849755
 0.03764393 0.33919254 0.04493255 0.84713701 0.82798093 0.53887536
 0.86911183 0.03681373 0.19558676 0.92803899 0.80125731 0.01494264
 0.47895211 0.39999993 0.98804659 0.62017226 0.04140532 0.90444788
 0.16550782 0.80125731 0.85373558 0.06600189 0.14758199 0.01457845
 0.09322794 0.02224573 0.93347502 0.64414562 0.82571666 0.923938

In [ ]:
# 予測結果を閾値を設定して1, 0に置換する
predict_test_target = np.where(predict_test_target < 0.5, 0, 1)

In [ ]:
print(predict_test_target)

[0 0 0 0 1 0 0 0 1 0 0 0 1 0 1 1 0 0 1 0 0 1 1 1 1 0 1 0 1 0 0 0 1 1 1 0 0
 0 0 1 0 1 0 1 1 0 0 0 1 1 1 0 1 1 0 0 0 0 0 1 0 0 0 1 1 1 1 0 0 1 1 0 0 0
 1 1 0 1 0 1 1 0 0 0 0 0 1 1 1 1 1 0 1 0 1 0 1 0 1 0 1 0 0 0 1 0 0 0 0 0 0
 1 1 1 1 0 0 1 1 1 1 0 1 0 0 1 0 1 0 0 0 0 1 0 0 0 0 0 0 0 0 1 0 0 1 0 0 0
 1 0 1 0 0 1 0 0 1 1 1 1 1 1 1 0 0 1 0 0 1 0 0 0 0 0 0 1 1 0 1 1 0 1 1 0 1
 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 0 1 0 1 0 0 0 0 1 0 0 0 0 1 0 0 1 0 1 0 1 0
 1 0 1 1 0 1 0 0 0 1 0 0 0 0 0 0 1 1 1 1 0 0 0 0 1 0 1 0 1 0 1 0 0 0 0 0 1
 0 0 0 1 1 0 0 0 0 0 0 0 0 1 0 0 1 0 0 0 0 0 1 1 0 1 0 0 0 0 0 0 0 0 1 0 0
 1 0 0 0 0 0 0 0 1 1 0 1 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 1 1 0 1 0 0 0 1 0 0
 1 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 1 1 0 0 0 0 0 1 0 0 1 0 1 1 0 1 0 0 0 1 1
 0 1 0 0 1 1 0 0 0 1 0 0 0 1 0 1 0 0 0 1 0 1 1 0 0 1 0 1 0 0 1 0 1 0 0 0 0
 0 1 1 1 1 0 0 1 0 0 1]


<a id="5"></a>
# <div style= "font-family: Cambria; font-weight: bold; letter-spacing: 0px; color: white; font-size: 120%; text-align: left; padding: 3.0px; background: #006036; border-bottom: 8px solid #D0A900" > SUBMISSION<br> <div>

In [ ]:
# 提出の準備
submission = pd.DataFrame({'PassengerId' : test['PassengerId'],
                           'Survived' : predict_test_target})

submission.head()

PassengerId  Survived
0          892         0
1          893         0
2          894         0
3          895         0
4          896         1

In [ ]:
submission.to_csv('submission_lightFBM_1.csv', index = False)